In [1]:
!pip install -U datasets -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.8/50.8 kB 866.3 kB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 471.6/471.6 kB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 3.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 177.6/177.6 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 20.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 239.5/239.5 kB 14.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.6/124.6 kB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 447.9/447.9 kB 18.0 MB/s eta 0:00:00


In [2]:
from datasets import load_dataset
import re
import random

def split_into_paragraphs(text):
    # Split by markdown headers or double newlines
    paragraphs = re.split(r'\n\n|(?=^#)', text, flags=re.MULTILINE)
    return [p.strip() for p in paragraphs if p.strip()]

def create_input_output_pairs(example):
    paragraphs = example['paragraphs']
    n_paragraphs = len(paragraphs)

    # Randomly select about half of the paragraphs for input
    n_input = max(1, random.randint(n_paragraphs // 2 - 1, n_paragraphs // 2 + 1))

    input_paragraphs = paragraphs[:n_input]
    output_paragraphs = paragraphs[n_input:]

    return {
        'inputs': ' '.join(input_paragraphs),
        'targets': ' '.join(output_paragraphs)
    }

def preprocess_dataset(dataset_name, text_column='text'):
    # Load the dataset
    dataset = load_dataset(dataset_name)

    # Split text into paragraphs
    dataset = dataset.map(
        lambda example: {'paragraphs': split_into_paragraphs(example[text_column])},
        remove_columns=[text_column]
    )

    # Create input-output pairs
    preprocessed_dataset = dataset.map(
        create_input_output_pairs,
        remove_columns=['paragraphs']
    )

    return preprocessed_dataset





In [3]:
dataset_name = 'euirim/goodwiki'

preprocessed_dataset = preprocess_dataset(dataset_name, text_column='markdown')

# Print some examples
print(preprocessed_dataset['train'][:5])

README.md:   0%|          | 0.00/10.4k [00:00<?, ?B/s]

09_04_2023_v1.parquet:   0%|          | 0.00/483M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/44754 [00:00<?, ? examples/s]

Map:   0%|          | 0/44754 [00:00<?, ? examples/s]

Map:   0%|          | 0/44754 [00:00<?, ? examples/s]

{'pageid': [57185536, 15394015, 62958021, 17546, 13280513], 'title': ['Georgia Hopley', 'Willis Ward', 'Instant Replay Game', 'Louvre', 'Launch Party'], 'revid': [1163683705, 1170257280, 1166130448, 1172724876, 1150875056], 'description': ['American journalist and temperance advocate', 'Track and field athlete and American football player', 'Notable American football game', 'Art museum in Paris, France', None], 'categories': [['1858 births', '1944 deaths', '19th-century American journalists', '19th-century American women journalists', '19th-century American women writers', '20th-century American journalists', '20th-century American women journalists', 'American temperance activists', 'Hopley family', 'Journalists from Ohio', 'Ohio Republicans', 'People from Bucyrus, Ohio'], ['1912 births', '1983 deaths', '20th-century African-American lawyers', '20th-century African-American sportspeople', '20th-century American lawyers', 'African-American players of American football', 'American footb

In [4]:
preprocessed_dataset.push_to_hub("pszemraj/goodwiki-text2text-completion", private=True)

Uploading the dataset shards:   0%|          | 0/2 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/23 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/23 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co/datasets/pszemraj/goodwiki-text2text-completion/commit/0e77d141a0567fed9cd9b65e56a97d83e97d0452', commit_message='Upload dataset', commit_description='', oid='0e77d141a0567fed9cd9b65e56a97d83e97d0452', pr_url=None, pr_revision=None, pr_num=None)